# DNN project - Watermarks detection using YOLO

In [1]:
!pip install lightning -qqq
!pip install ultralytics -qqq
!pip install datasets -qqq
!pip install wget -qqq
!pip install torchmetrics -qqq
!pip install torchmetrics[detection] -qqq
!pip install pycocotool -qqq
!pip install faster-coco-eval -qqq

ERROR: Could not find a version that satisfies the requirement pycocotool (from versions: none)
ERROR: No matching distribution found for pycocotool


In [2]:
import lightning as pl
import torch
import torch.nn as nn
import torchvision.models as models
import torchvision
from ultralytics import YOLO
from datasets import load_dataset
from torch.utils.data import DataLoader
from ultralytics.utils.benchmarks import benchmark
from torchmetrics.detection import MeanAveragePrecision
from pprint import pprint

## Dataset

In [5]:
!pip install -qqq wget
import wget
import zipfile
import os

for i in ["train-yolo", "test-yolo", "val-yolo"]:
    wget.download(f"https://huggingface.co/datasets/bastienp/visible-watermark-pita/resolve/main/data/{i}.zip?download=true")

    with zipfile.ZipFile(f"{i}.zip", "r") as zip_ref:
        zip_ref.extractall("data")
    os.remove(f'{i}.zip')

In [6]:
# doesn't set correctly the path inside the file, better to import it by hand in Kaggle
wget.download(
            "https://huggingface.co/datasets/bastienp/visible-watermark-pita/resolve/main/data/metadata.yml?download=true",
            out="data/metadata.yml",
        )

'data/metadata.yml'

## Training with Ultralytics

In [6]:
DATA_PATH = "/kaggle/input/metadata"

In [8]:
yolo = YOLO('yolov8l.pt')
results = yolo.train(data=f'{DATA_PATH}/metadata.yml', epochs=15, imgsz=512, batch=32)

100%|██████████| 83.7M/83.7M [00:00<00:00, 230MB/s] 


Ultralytics YOLOv8.1.9 🚀 Python-3.10.13 torch-2.1.2 CUDA:0 (Tesla P100-PCIE-16GB, 16276MiB)
engine/trainer: task=detect, mode=train, model=yolov8l.pt, data=/kaggle/input/metadata/metadata.yml, epochs=15, time=None, patience=50, batch=32, imgsz=512, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_con

100%|██████████| 755k/755k [00:00<00:00, 14.3MB/s]
2024-02-03 08:16:28,027	INFO util.py:124 -- Outdated packages:
  ipywidgets==7.7.1 found, needs ipywidgets>=8
Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-02-03 08:16:28,490	INFO util.py:124 -- Outdated packages:
  ipywidgets==7.7.1 found, needs ipywidgets>=8
Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.
2024-02-03 08:16:30.802203: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-02-03 08:16:30.802308: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-02-03 08:16:30.943912: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS facto

Overriding model.yaml nc=80 with nc=2

                   from  n    params  module                                       arguments                     
  0                  -1  1      1856  ultralytics.nn.modules.conv.Conv             [3, 64, 3, 2]                 
  1                  -1  1     73984  ultralytics.nn.modules.conv.Conv             [64, 128, 3, 2]               
  2                  -1  3    279808  ultralytics.nn.modules.block.C2f             [128, 128, 3, True]           
  3                  -1  1    295424  ultralytics.nn.modules.conv.Conv             [128, 256, 3, 2]              
  4                  -1  6   2101248  ultralytics.nn.modules.block.C2f             [256, 256, 6, True]           
  5                  -1  1   1180672  ultralytics.nn.modules.conv.Conv             [256, 512, 3, 2]              
  6                  -1  6   8396800  ultralytics.nn.modules.block.C2f             [512, 512, 6, True]           
  7                  -1  1   2360320  ultralytics

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit:

...

                   all       3913       3913      0.981      0.975      0.993      0.923

      Epoch    GPU_mem   box_loss   cls_loss   dfl_loss  Instances       Size


      15/15      13.2G     0.4619     0.3008      0.947         27        512: 100%|██████████| 387/387 [06:53<00:00,  1.07s/it]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 62/62 [00:55<00:00,  1.12it/s]


                   all       3913       3913      0.979      0.979      0.994      0.923

15 epochs completed in 1.978 hours.
Optimizer stripped from runs/detect/train/weights/last.pt, 87.6MB
Optimizer stripped from runs/detect/train/weights/best.pt, 87.6MB

Validating runs/detect/train/weights/best.pt...
Ultralytics YOLOv8.1.9 🚀 Python-3.10.13 torch-2.1.2 CUDA:0 (Tesla P100-PCIE-16GB, 16276MiB)
Model summary (fused): 268 layers, 43608150 parameters, 0 gradients, 164.8 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 62/62 [00:59<00:00,  1.04it/s]


                   all       3913       3913      0.984      0.972      0.993      0.924
                  logo       3913       2000      0.986       0.98      0.994      0.922
                  text       3913       1913      0.981      0.964      0.992      0.926
Speed: 0.1ms preprocess, 11.5ms inference, 0.0ms loss, 0.9ms postprocess per image
Results saved to runs/detect/train


In [9]:
metrics = yolo.val()
metrics

Ultralytics YOLOv8.1.9 🚀 Python-3.10.13 torch-2.1.2 CUDA:0 (Tesla P100-PCIE-16GB, 16276MiB)
Model summary (fused): 268 layers, 43608150 parameters, 0 gradients, 164.8 GFLOPs


val: Scanning /kaggle/working/data/val-yolo/labels.cache... 3913 images, 0 backgrounds, 0 corrupt: 100%|██████████| 3913/3913 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 123/123 [01:03<00:00,  1.92it/s]


                   all       3913       3913      0.983      0.972      0.993      0.925
                  logo       3913       2000      0.986       0.98      0.994      0.923
                  text       3913       1913       0.98      0.965      0.992      0.926
Speed: 0.1ms preprocess, 12.8ms inference, 0.0ms loss, 1.0ms postprocess per image
Results saved to runs/detect/train2


ultralytics.utils.metrics.DetMetrics object with attributes:

ap_class_index: array([0, 1])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x7d6a2c0fcca0>
curves: ['Precision-Recall(B)', 'F1-Confidence(B)', 'Precision-Confidence(B)', 'Recall-Confidence(B)']
curves_results: [[array([          0,    0.001001,    0.002002,    0.003003,    0.004004,    0.005005,    0.006006,    0.007007,    0.008008,    0.009009,     0.01001,    0.011011,    0.012012,    0.013013,    0.014014,    0.015015,    0.016016,    0.017017,    0.018018,    0.019019,     0.02002,    0.021021,    0.022022,    0.023023,
          0.024024,    0.025025,    0.026026,    0.027027,    0.028028,    0.029029,     0.03003,    0.031031,    0.032032,    0.033033,    0.034034,    0.035035,    0.036036,    0.037037,    0.038038,    0.039039,     0.04004,    0.041041,    0.042042,    0.043043,    0.044044,    0.045045,    0.046046,    0.047047,
          0.04804

### Metrics - Nano

The best.pt file was downloaded from Weights & Biases and used to evaluate the model on the test set. The results are shown below.

In [11]:
TEST_DATA_PATH = "/kaggle/input/ultralytics-bench"
BEST_MODEL_PATH = "/kaggle/input/yolo-best/best.pt"

benchmark(model=BEST_MODEL_PATH, data=f'{TEST_DATA_PATH}/metadata_bench.yml', imgsz=512, device=0)

In [24]:
model = YOLO(BEST_MODEL_PATH)
TEST_PATH = "/kaggle/working/data/test-yolo"
results = model(f"{TEST_PATH}/images", stream=True, verbose=False)

preds = []
targets = []
for result in results:
    dict_res = dict(
        boxes=result.boxes.xywhn.cpu(),
        scores=result.boxes.conf.cpu(),
        labels=result.boxes.cls.cpu().int()
    )
    preds.append(dict_res)
    img_path = result.path
    img_id = img_path.split("/")[-1].split(".")[0]
    labels_path = f"{TEST_PATH}/labels/{img_id}.txt"
    with open(labels_path, "r") as f:
        lines = f.readlines()
        boxes = []
        classes = []
        for line in lines:
            box = list(map(float, line.strip().split(" ")))
            classes.append(int(box[0]))
            box = box[1:]
            boxes.append(box)
        dict_targets = {
            "boxes": torch.tensor(boxes),
            "labels": torch.tensor(classes)
        }
        targets.append(dict_targets)

In [24]:
pred = preds[0]
target = targets[0]
pred, target

({'boxes': tensor([[0.2073, 0.8510, 0.2894, 0.0658]]),
  'scores': tensor([0.8605]),
  'labels': tensor([1], dtype=torch.int32)},
 {'boxes': tensor([[0.2109, 0.8477, 0.3203, 0.0645]]), 'labels': tensor([1])})

In [25]:
metric = MeanAveragePrecision(iou_type="bbox", box_format="cxcywh", class_metrics=True)
metric.update(preds, targets)

In [26]:
pprint(metric.compute())

{'classes': tensor([0, 1], dtype=torch.int32),
 'map': tensor(0.8750),
 'map_50': tensor(0.9690),
 'map_75': tensor(0.9415),
 'map_large': tensor(-1.),
 'map_medium': tensor(-1.),
 'map_per_class': tensor([0.8643, 0.8858]),
 'map_small': tensor(0.8750),
 'mar_1': tensor(0.8905),
 'mar_10': tensor(0.8933),
 'mar_100': tensor(0.8933),
 'mar_100_per_class': tensor([0.8857, 0.9008]),
 'mar_large': tensor(-1.),
 'mar_medium': tensor(-1.),
 'mar_small': tensor(0.8933)}


### Metrics - Large

In [11]:
TEST_DATA_PATH = "/kaggle/input/ultralytics-bench"
BEST_MODEL_PATH = "/kaggle/input/yolo-best/large_best.pt"

benchmark(model=BEST_MODEL_PATH, data=f'{TEST_DATA_PATH}/metadata_bench.yml', imgsz=512, device=0)

Setup complete ✅ (4 CPUs, 31.4 GB RAM, 5433.3/8062.4 GB disk)

Benchmarks complete for large_best.pt on /kaggle/input/ultralytics-bench/metadata_bench.yml at imgsz=512 (144.23s)
                   Format Status❔  Size (MB)  metrics/mAP50-95(B)  Inference time (ms/im)
0                 PyTorch       ✅       83.6               0.9259                   20.86
1             TorchScript       ❌        0.0                  NaN                     NaN
2                    ONNX       ❌        0.0                  NaN                     NaN
3                OpenVINO       ❌        0.0                  NaN                     NaN
4                TensorRT       ❌        0.0                  NaN                     NaN
5                  CoreML       ❌        0.0                  NaN                     NaN
6   TensorFlow SavedModel       ❌        0.0                  NaN                     NaN
7     TensorFlow GraphDef       ❌        0.0                  NaN                     NaN
8         Te

Format Status❔  Size (MB)  metrics/mAP50-95(B)  Inference time (ms/im)
0                 PyTorch       ✅       83.6               0.9259                   20.86
1             TorchScript       ❌        0.0                  NaN                     NaN
2                    ONNX       ❌        0.0                  NaN                     NaN
3                OpenVINO       ❌        0.0                  NaN                     NaN
4                TensorRT       ❌        0.0                  NaN                     NaN
5                  CoreML       ❌        0.0                  NaN                     NaN
6   TensorFlow SavedModel       ❌        0.0                  NaN                     NaN
7     TensorFlow GraphDef       ❌        0.0                  NaN                     NaN
8         TensorFlow Lite       ❌        0.0                  NaN                     NaN
9     TensorFlow Edge TPU       ❌        0.0                  NaN                     NaN
10          TensorFlow.js       ❌        0.0                  NaN                     NaN
11           PaddlePaddle       ❌        0.0                  NaN                     NaN
12                   ncnn       ❌        0.0                  NaN                     NaN

In [27]:
BEST_MODEL_PATH = "/kaggle/input/yolo-best/large_best.pt"

In [28]:
model = YOLO(BEST_MODEL_PATH)
TEST_PATH = "/kaggle/working/data/test-yolo"
results = model(f"{TEST_PATH}/images", stream=True, verbose=False)

preds = []
targets = []
for result in results:
    dict_res = dict(
        boxes=result.boxes.xywhn.cpu(),
        scores=result.boxes.conf.cpu(),
        labels=result.boxes.cls.cpu().int()
    )
    preds.append(dict_res)
    img_path = result.path
    img_id = img_path.split("/")[-1].split(".")[0]
    labels_path = f"{TEST_PATH}/labels/{img_id}.txt"
    with open(labels_path, "r") as f:
        lines = f.readlines()
        boxes = []
        classes = []
        for line in lines:
            box = list(map(float, line.strip().split(" ")))
            classes.append(int(box[0]))
            box = box[1:]
            boxes.append(box)
        dict_targets = {
            "boxes": torch.tensor(boxes),
            "labels": torch.tensor(classes)
        }
        targets.append(dict_targets)

In [29]:
metric = MeanAveragePrecision(iou_type="bbox", box_format="cxcywh", class_metrics=True)
metric.update(preds, targets)
pprint(metric.compute())

{'classes': tensor([0, 1], dtype=torch.int32),
 'map': tensor(0.8900),
 'map_50': tensor(0.9741),
 'map_75': tensor(0.9473),
 'map_large': tensor(-1.),
 'map_medium': tensor(-1.),
 'map_per_class': tensor([0.8783, 0.9018]),
 'map_small': tensor(0.8900),
 'mar_1': tensor(0.9079),
 'mar_10': tensor(0.9098),
 'mar_100': tensor(0.9098),
 'mar_100_per_class': tensor([0.8992, 0.9204]),
 'mar_large': tensor(-1.),
 'mar_medium': tensor(-1.),
 'mar_small': tensor(0.9098)}


## Test on CLWD dataset

In [15]:
!pip install gdown

In [16]:
!gdown --id 1844cm684CLgZf1tYtgD1nbcFshGE-mgF

/opt/conda/lib/python3.10/site-packages/gdown/cli.py:132: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  warnings.warn(
Downloading...
From (original): https://drive.google.com/uc?id=1844cm684CLgZf1tYtgD1nbcFshGE-mgF
From (redirected): https://drive.google.com/uc?id=1844cm684CLgZf1tYtgD1nbcFshGE-mgF&confirm=t&uuid=da39f8b4-354e-4b93-af2e-b24c88a097ed
To: /kaggle/working/train-yolo.zip
100%|████████████████████████████████████████| 841M/841M [00:09<00:00, 88.3MB/s]


In [17]:
%mkdir tmp_data

In [18]:
! unzip train-yolo.zip -d tmp_data

Archive:  train-yolo.zip
   creating: tmp_data/train-yolo/
   creating: tmp_data/train-yolo/images/
   creating: tmp_data/train-yolo/labels/
  inflating: tmp_data/train-yolo/images/9733.jpg  
  inflating: tmp_data/train-yolo/images/14147.jpg  
  inflating: tmp_data/train-yolo/images/52112.jpg  
  inflating: tmp_data/train-yolo/images/63.jpg  
  inflating: tmp_data/train-yolo/images/6400.jpg  
  inflating: tmp_data/train-yolo/images/34297.jpg  
  inflating: tmp_data/train-yolo/images/42301.jpg  
  inflating: tmp_data/train-yolo/images/24084.jpg  
  inflating: tmp_data/train-yolo/images/13628.jpg  
  inflating: tmp_data/train-yolo/images/23933.jpg  
  inflating: tmp_data/train-yolo/images/12536.jpg  
  inflating: tmp_data/train-yolo/images/54563.jpg  
  inflating: tmp_data/train-yolo/images/823.jpg  
  inflating: tmp_data/train-yolo/images/15259.jpg  
  inflating: tmp_data/train-yolo/images/35189.jpg  
  inflating: tmp_data/train-yolo/images/44770.jpg  
  inflating: tmp_data/train-yolo/i

In [30]:
BEST_MODEL_PATH = "/kaggle/input/yolo-best/best.pt"
model = YOLO(BEST_MODEL_PATH)
TEST_PATH = "/kaggle/working/tmp_data/train-yolo"
results = model(f"{TEST_PATH}/images", stream=True, verbose=False)

preds = []
targets = []
i = 0
for result in results:
    i += 1
    if i % 1000 == 0:
        print(i)
    dict_res = dict(
        boxes=result.boxes.xywhn.cpu(),
        scores=result.boxes.conf.cpu(),
        labels=result.boxes.cls.cpu().int()
    )
    preds.append(dict_res)
    img_path = result.path
    img_id = img_path.split("/")[-1].split(".")[0]
    labels_path = f"{TEST_PATH}/labels/{img_id}.txt"
    with open(labels_path, "r") as f:
        lines = f.readlines()
        boxes = []
        classes = []
        for line in lines:
            box = list(map(float, line.strip().split(" ")))
            classes.append(int(box[0]))
            box = box[1:]
            boxes.append(box)
        dict_targets = {
            "boxes": torch.tensor(boxes),
            "labels": torch.tensor(classes)
        }
        targets.append(dict_targets)

1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000


In [31]:
metric = MeanAveragePrecision(iou_type="bbox", box_format="cxcywh", class_metrics=True)
metric.update(preds, targets)
pprint(metric.compute())

{'classes': tensor([0, 1], dtype=torch.int32),
 'map': tensor(0.0190),
 'map_50': tensor(0.0394),
 'map_75': tensor(0.0160),
 'map_large': tensor(-1.),
 'map_medium': tensor(-1.),
 'map_per_class': tensor([ 0.0190, -1.0000]),
 'map_small': tensor(0.0190),
 'mar_1': tensor(0.0288),
 'mar_10': tensor(0.0297),
 'mar_100': tensor(0.0297),
 'mar_100_per_class': tensor([ 0.0297, -1.0000]),
 'mar_large': tensor(-1.),
 'mar_medium': tensor(-1.),
 'mar_small': tensor(0.0297)}
